# GROUP-1: MongoDB → JSON → VECTOR (WORD2VEC)

In [1]:
from pymongo import MongoClient
import json
from gensim.models import Word2Vec
import nltk
from nltk.tokenize import word_tokenize
import itertools
import numpy as np
nltk.download('punkt')

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\ASUS\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

## 1. FUNCTION

In [2]:
# Connect to MongoDB
def connect_to_mongodb(host, port, db_name, collection_name):
    client = MongoClient(host, port)
    db = client[db_name]
    collection = db[collection_name]
    return collection
def read_json_from_mongodb(mongodb_collection):
    # MongoDB connection
    #collection = connect_to_mongodb(mongodb_host, mongodb_port, mongodb_db_name, mongodb_collection_name)
    # Read all JSON documents from the collection
    cursor = mongodb_collection.find({})
    json_documents = [doc for doc in cursor]

    return json_documents
def dict_to_vectors(data):
    flat_data = []
    for sublist in data.values():
        for sentence_list in sublist:
            for sentence in sentence_list:
                flat_data.append(sentence)

    tokenized_data = [word_tokenize(sentence) for sentence in flat_data]

    model = Word2Vec(sentences=tokenized_data, vector_size=100, window=5, min_count=1, workers=4)

    # Aggregate vectors of all words and compute the average
    vectors = [model.wv[word] for sentence in tokenized_data for word in sentence if word in model.wv]
    if vectors:
        avg_vector = np.mean(vectors, axis=0)
    else:
        avg_vector = None

    return avg_vector
# Insert vector into MongoDB
def insert_vector(collection, vector, custom_id):
    collection.insert_one({'_id': custom_id, 'vector': vector.tolist()})

## 2. STATIC VARIABLE

In [3]:
mongodb_connection = r'mongodb://localhost:27017/'
database_name = "metaLeak"
collection_name = "jsonGroup1"
index_name = "group1-vector"
mongodb_host = "localhost"
mongodb_port = 27017
mongodb_db_name = "metaLeak"
json_collection_name = "jsonGroup1"
vector_collection_name = "vectorGroup1"
#doc_id = "your_document_id"
vector_field_name = "vector"

## 3. MAIN

In [4]:
json_collection = connect_to_mongodb(mongodb_host, mongodb_port, mongodb_db_name, json_collection_name)
vector_collection = connect_to_mongodb(mongodb_host, mongodb_port, mongodb_db_name, vector_collection_name)
json_documents = read_json_from_mongodb(json_collection)
#print(json_documents)
#print(len(json_documents))
for i in range(len(json_documents)):
    print("-----------------------------------Loop "+str(i)+"-----------------------------------")
    doc_id = json_documents[i]["_id"]
    print(doc_id)
    data_static_declare = json_documents[i]['data'][0]
    print(data_static_declare)
    print(type(data_static_declare))
    vector = dict_to_vectors(data_static_declare)
    print(vector)
    print(type(vector))
    insert_vector(vector_collection, vector,doc_id)
    #break

-----------------------------------Loop 0-----------------------------------
16-Megapixel-HDr-Camera-1.1.json
{'static_declare': [['private static final String TAG = "ImageSaver";', 'private static final String TAG_GPS_IMG_DIRECTION = "GPSImgDirection";', 'private static final String TAG_GPS_IMG_DIRECTION_REF = "GPSImgDirectionRef";']]}
<class 'dict'>
[-1.9982920e-03  1.5143775e-03  5.5949169e-04  9.5013430e-04
 -6.8349109e-05 -9.6970395e-04  1.9582456e-03  3.0939563e-03
 -3.3777719e-03 -2.5127034e-03  8.1653375e-04 -8.1824593e-04
 -9.4314892e-04  1.3705531e-04  8.4182888e-04 -1.1397798e-03
  3.0301558e-03  1.5116293e-03 -2.8576131e-03 -4.4880966e-03
 -4.0291075e-04 -9.1489422e-04  5.4696891e-03 -1.0370297e-04
 -4.0510713e-04  6.6277559e-04 -4.9028837e-04  1.8071241e-03
 -2.4370821e-03  2.2913949e-03  2.3893055e-03 -1.1132323e-03
 -1.3117824e-04 -3.1424768e-03 -4.2355453e-04  1.2278401e-03
  1.0108819e-03 -2.4635594e-05 -9.3926559e-04  9.4184965e-05
  1.9769494e-03 -1.3836219e-03 -2.40

[-0.02170241  0.16370864  0.09079482 -0.03208135  0.12809862 -0.08507361
  0.22431912  0.36522806 -0.26479325 -0.2843214   0.14289165 -0.20200951
 -0.04659906  0.02767829  0.08438152 -0.12645714  0.2404881   0.06653742
 -0.1655557  -0.440873    0.00673271 -0.10785421  0.42706814 -0.05402908
 -0.02599354  0.03917295 -0.00133928  0.01004786 -0.08822006  0.12184018
  0.17217334 -0.0920866  -0.02129742 -0.1869481  -0.05892859  0.13263772
  0.11017919 -0.00994648 -0.05571319 -0.16243601  0.14498466 -0.13772717
 -0.16325432  0.10458396  0.16003408  0.03303124 -0.07296373 -0.09494329
 -0.05340673  0.08164047  0.06236574 -0.20833556 -0.15284479 -0.1253969
 -0.21796449 -0.15856989  0.02858389 -0.09505923 -0.0549577  -0.07490373
 -0.03607551 -0.10011688  0.35769296  0.00962722 -0.21780717  0.36775213
  0.03368321  0.12286955 -0.32483128  0.02509896  0.0239233   0.34502143
  0.13346916  0.19086806  0.09010487  0.03471105  0.1049072   0.16412184
 -0.09304158 -0.00208004 -0.07939798 -0.05859892  0.

[-1.86002046e-01  1.57556057e-01 -3.79821733e-02  4.10918668e-02
  5.63728623e-02 -8.21881369e-02  7.57541135e-02  2.58444846e-01
 -1.17964149e-01 -9.13792178e-02  3.40470225e-02 -1.29912242e-01
 -6.58070445e-02  2.03424841e-02  4.75124344e-02 -1.37121186e-01
  1.31640613e-01  1.99750885e-02 -2.08912909e-01 -1.46506310e-01
 -7.18008028e-03 -7.46343210e-02  2.76303291e-01 -7.47930398e-03
  1.27009759e-02  9.42315848e-04  1.02981068e-01  1.01441905e-01
 -1.66080430e-01  7.58233517e-02  2.03651443e-01 -1.89625815e-01
 -9.50769037e-02 -2.57557213e-01  1.57201309e-02  1.22991063e-01
  2.69546598e-01  6.58332705e-02 -2.37436742e-02  7.91911930e-02
  4.13621739e-02 -5.93196526e-02 -1.77423850e-01 -1.20662013e-02
  1.66005939e-01  4.57967408e-02 -8.85913335e-03  4.98135947e-02
  5.50320260e-02  2.28829943e-02  8.46459419e-02 -8.44884142e-02
  1.04221814e-04 -4.94812243e-02 -1.57917663e-01 -8.13477236e-05
  1.22215144e-01 -5.60738742e-02 -1.63185686e-01 -2.98276334e-03
  2.96278149e-02 -5.88774

[-2.12242633e-01  1.68512329e-01 -1.72205921e-02  6.59579039e-02
  7.47095421e-02 -1.07875139e-01  6.80495277e-02  2.79072791e-01
 -1.68206036e-01 -8.86692181e-02 -9.61621478e-03 -8.98768604e-02
 -8.13383162e-02  5.65952435e-02  4.71486561e-02 -1.40286535e-01
  1.51056796e-01  1.20353803e-01 -1.94604844e-01 -1.85788527e-01
  4.29077521e-02 -1.18818246e-01  2.94380099e-01 -1.98749406e-03
 -1.99702390e-05 -7.54568130e-02  2.31780745e-02  6.46260306e-02
 -1.70349598e-01  8.08878243e-02  2.02959672e-01 -1.30766541e-01
 -4.94621247e-02 -2.11988732e-01  2.65180897e-02  1.37997672e-01
  2.05035195e-01  1.28855957e-02  2.15069856e-02  5.07396124e-02
  7.17703477e-02 -8.44226331e-02 -1.65891811e-01 -1.41478404e-02
  7.56585747e-02  2.31662616e-02  1.68324728e-02  1.56456269e-02
  3.83136086e-02  1.11896498e-02  4.45776209e-02 -1.11176409e-01
 -2.38246527e-02 -8.69988501e-02 -1.27859131e-01  8.55747424e-03
  6.34607598e-02 -4.77574579e-02 -8.87635723e-02 -7.26375356e-02
  8.05308223e-02  4.88710

[-0.17537609  0.12568898  0.01327347  0.13423206  0.07952712 -0.04329656
  0.12447969  0.13066776 -0.17260493 -0.04273829  0.06728902 -0.11740438
  0.0657156  -0.01496456  0.13606459 -0.02616667  0.04902659  0.0321942
 -0.16040446 -0.15381949  0.02229615  0.02993101  0.24529152 -0.07707429
  0.03813845 -0.01284574 -0.01278651 -0.02465423 -0.06677454  0.00731669
  0.17133726 -0.1286119   0.04269178 -0.03600065 -0.04159168  0.09347257
  0.04622617  0.06159686  0.01412563 -0.03830829  0.01099881 -0.03341099
 -0.09031209  0.0016409   0.06397218  0.0195912   0.00268926  0.04221768
 -0.01700749 -0.00746401  0.04235986 -0.05468255 -0.04254448 -0.12354188
 -0.06994542 -0.06767256  0.04632984 -0.03462067  0.01822181 -0.08479112
 -0.07818677 -0.05231886  0.22038539 -0.03729662 -0.14179125  0.12362096
  0.01507894  0.15948248 -0.16748875  0.06780428 -0.02457685  0.08412624
  0.11856709  0.15075517 -0.0316766   0.02511625 -0.00237752 -0.03055911
 -0.0930483  -0.06689105 -0.08270086 -0.10174569  0.

...

[-0.23727491  0.13670038  0.10284724  0.22492313  0.0872831  -0.12902474
  0.28066018  0.3305852  -0.3468942  -0.1570345   0.06312475 -0.17896551
 -0.02933815  0.07865215  0.1296431  -0.15022852  0.18120214  0.10437866
 -0.3228143  -0.4861095  -0.00148549 -0.01680827  0.4624746  -0.09228959
  0.01202224  0.04461764  0.00586887  0.05355977 -0.29555058  0.08363668
  0.25024277 -0.20512538 -0.08438569 -0.20403786 -0.11744603  0.1687235
  0.08966281  0.02377709 -0.0746527  -0.10028837  0.21874952 -0.11134833
 -0.16783597  0.05590286  0.18750426  0.0903913  -0.13851736  0.0237817
  0.02169795  0.0674773   0.00536052 -0.22821629 -0.08260276 -0.0901778
 -0.36106867 -0.06695551  0.03588986 -0.18913864 -0.2301301  -0.08843114
  0.09501979 -0.02666779  0.2885411  -0.01515821 -0.19411701  0.33346435
 -0.03144843  0.33326668 -0.35379392  0.02223968  0.02103637  0.30009067
  0.21991388  0.1558131   0.04963616  0.04906227  0.04416554  0.07033235
 -0.09633396 -0.15453897 -0.15644133 -0.18662763 -0.01

[-0.13887891  0.13402712  0.07354171  0.07111768  0.05663436 -0.15466908
  0.08175113  0.29662263 -0.16733757 -0.14716053  0.05950822 -0.16559887
  0.02061853  0.02907236  0.09073501 -0.07559699  0.18340823  0.04544652
 -0.12211493 -0.32719165  0.06053531 -0.01193136  0.2589912  -0.05253735
 -0.01168624  0.04477876 -0.11392766  0.04887878 -0.08521757  0.08498096
  0.1919532  -0.07727317  0.03948509 -0.12494719 -0.03822203  0.1278814
  0.07536876 -0.00630721 -0.06721863 -0.10450485  0.07115758 -0.06313412
 -0.11991631  0.08022738  0.04341111 -0.01032742 -0.09646765 -0.04204446
  0.02830568  0.02529252  0.06058608 -0.13628022 -0.08600672 -0.03339881
 -0.13078415 -0.06356526  0.07434002 -0.0512549  -0.01838193  0.00884721
 -0.04780911 -0.03735371  0.20471594 -0.06080248 -0.1729272   0.17109674
  0.04400016  0.12234186 -0.19656458  0.01039729  0.00392201  0.15133688
  0.12413705  0.12192547  0.06156686  0.04135337  0.06220759  0.04510167
 -0.04686466 -0.06629225 -0.1906856  -0.06553565  0.

[-0.31804866  0.2841803  -0.02800232  0.02639434  0.13681917 -0.18167688
  0.1405599   0.43115667 -0.22337392 -0.18692517 -0.00578246 -0.1891792
 -0.09410283  0.06832796  0.14800617 -0.09701082  0.2630427   0.07221165
 -0.21363476 -0.28577536  0.03889624 -0.13883218  0.4122326  -0.00614181
 -0.03628401 -0.02440104  0.02997621  0.12726359 -0.15646231  0.05153814
  0.30363247 -0.19398503 -0.10528972 -0.342288    0.12099808  0.19448079
  0.23275034  0.02035469 -0.04670905  0.04386819  0.20002769 -0.17499252
 -0.16846062  0.08337009  0.16525339  0.03802551  0.03220313 -0.01681691
 -0.02478885 -0.01503774  0.22030394 -0.22220896 -0.16538773 -0.07087122
 -0.23919418 -0.0572359   0.16310692 -0.03916576 -0.18400653 -0.10126515
  0.04537645 -0.01122518  0.21243297 -0.08597336 -0.13249482  0.23583548
  0.22230066  0.20989096 -0.25725406  0.02345334 -0.03335246  0.14220138
  0.17746809  0.25391623  0.12123994  0.12068559 -0.09700648  0.16892521
 -0.04808985 -0.10154712 -0.22525707 -0.11552985  0.

[ 0.01551015  0.03472887  0.04814151  0.13952719 -0.01119241 -0.08930018
  0.16291627  0.19295578 -0.25317317 -0.22609076 -0.00871127 -0.10966523
 -0.01985953  0.04531057  0.09944829 -0.05844514  0.15260507  0.03449299
 -0.07474745 -0.23559122  0.06755441  0.00506454  0.2223905  -0.10895658
  0.01494512  0.03250006 -0.09788469  0.10593328 -0.12052611  0.16037768
  0.07844133 -0.07826256  0.02273576 -0.18662393 -0.0133503   0.09827946
 -0.02125074  0.05921403 -0.0047743  -0.05759722  0.09956495 -0.10579463
 -0.05492235  0.14154226  0.13053448 -0.05969424 -0.11464801 -0.05092029
  0.15881313  0.02775392 -0.07041538 -0.02055617  0.06015651 -0.14994459
 -0.03340256  0.05712175 -0.04149551 -0.00266404 -0.00466166  0.05870155
  0.05116448 -0.03060095  0.13331454  0.06719138 -0.0322557   0.2289086
  0.05933637  0.2805272  -0.11656278 -0.03413463  0.03487387  0.05319473
  0.1030786   0.09374633  0.06958711  0.08883712  0.1249309   0.07887288
 -0.00088744 -0.20910443 -0.19395101 -0.08111462  0.

[-0.20213574  0.18817432  0.00634058  0.11074591  0.06647412 -0.12442115
  0.0833938   0.3593893  -0.32324797 -0.19227874  0.05618649 -0.17507353
 -0.07383113  0.07276209  0.04715683 -0.06140388  0.32475606  0.03910792
 -0.19137065 -0.48945847  0.01151602 -0.08467466  0.43489337 -0.06628015
  0.00100386  0.09679558 -0.1253803   0.18505311 -0.1570053   0.137669
  0.3220398  -0.10066777  0.02807858 -0.18640333 -0.05465137  0.1686927
  0.13163653  0.00534289 -0.01210348 -0.0017778   0.18383297 -0.13190076
 -0.20090902  0.10225771  0.09718029  0.03142187 -0.04859025 -0.0666076
 -0.03153533  0.06343136  0.05514856 -0.22786048 -0.11878175 -0.02069414
 -0.19923243 -0.15521437  0.05841634 -0.17709942 -0.08985499 -0.04028443
 -0.02338282 -0.0755431   0.31653175 -0.02710079 -0.18343247  0.24756742
  0.16850238  0.16846135 -0.24018002  0.07184966  0.04063121  0.30959982
  0.11658717  0.1368514   0.08326066  0.05393092  0.08176778  0.11853939
 -0.06201132 -0.06905378 -0.13962714 -0.07296768  0.046